<a href="https://colab.research.google.com/github/shmilyface/DS-Unit-2-Linear-Models/blob/master/Copy_of_DS_Sprint_Challenge_5_Linear_Models.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

_Lambda School Data Science, Unit 2_
 
# Linear Models  Sprint Challenge: Predict home prices in Ames, Iowa 🏠💸

To demonstrate mastery on your Sprint Challenge, do all the required, numbered instructions in this notebook.

To earn a score of "3", also do all the stretch goals.

For your Sprint Challenge, you'll use historical housing data. There's a data dictionary at the bottom of the notebook. 

Run this code cell to load the dataset:





In [1]:
#check the data
import pandas as pd
URL = 'https://drive.google.com/uc?export=download&id=1522WlEW6HFss36roD_Cd9nybqSuiVcCK'
df = pd.read_csv(URL)
assert df.shape == (2904, 47)

In [2]:
df.head()

1st_Flr_SF  Bedroom_AbvGr Bldg_Type  Bsmt_Full_Bath  Bsmt_Half_Bath  \
0        1656              3      1Fam             1.0             0.0   
1         896              2      1Fam             0.0             0.0   
2        1329              3      1Fam             0.0             0.0   
3        2110              3      1Fam             1.0             0.0   
4         928              3      1Fam             0.0             0.0   

  Central_Air Condition_1 Condition_2 Electrical Exter_Cond  ... Roof_Style  \
0           Y        Norm        Norm      SBrkr         TA  ...        Hip   
1           Y       Feedr        Norm      SBrkr         TA  ...      Gable   
2           Y        Norm        Norm      SBrkr         TA  ...        Hip   
3           Y        Norm        Norm      SBrkr         TA  ...        Hip   
4           Y        Norm        Norm      SBrkr         TA  ...      Gable   

  SalePrice Sale_Condition Sale_Type  Street TotRms_AbvGrd  Utilities  \
0    215000         Normal       WD     Pave             7     AllPub   
1    105000         Normal       WD     Pave             5     AllPub   
2    172000         Normal       WD     Pave             6     AllPub   
3    244000         Normal       WD     Pave             8     AllPub   
4    189900         Normal       WD     Pave             6     AllPub   

   Year_Built Year_Remod/Add Yr_Sold  
0        1960           1960    2010  
1        1961           1961    2010  
2        1958           1958    2010  
3        1968           1968    2010  
4        1997           1998    2010  

[5 rows x 47 columns]

In [3]:
#mean SalePrice: 180383.689738

df.describe()

1st_Flr_SF  Bedroom_AbvGr  Bsmt_Full_Bath  Bsmt_Half_Bath  \
count  2904.000000    2904.000000     2904.000000     2904.000000   
mean   1158.257231       2.854339        0.431474        0.061639   
std     388.351648       0.827820        0.525073        0.246202   
min     334.000000       0.000000        0.000000        0.000000   
25%     876.750000       2.000000        0.000000        0.000000   
50%    1083.500000       3.000000        0.000000        0.000000   
75%    1383.000000       3.000000        1.000000        0.000000   
max    5095.000000       8.000000        3.000000        2.000000   

         Full_Bath  Gr_Liv_Area    Half_Bath  Kitchen_AbvGr       Lot_Area  \
count  2904.000000  2904.000000  2904.000000    2904.000000    2904.000000   
mean      1.562328  1497.853650     0.376722       1.044421   10130.199725   
std       0.551427   504.591527     0.501416       0.214260    7869.928702   
min       0.000000   334.000000     0.000000       0.000000    1300.000000   
25%       1.000000  1124.000000     0.000000       1.000000    7424.750000   
50%       2.000000  1440.500000     0.000000       1.000000    9429.000000   
75%       2.000000  1740.500000     1.000000       1.000000   11516.250000   
max       4.000000  5642.000000     2.000000       3.000000  215245.000000   

       MS_SubClass      Mo_Sold  Overall_Cond  Overall_Qual      SalePrice  \
count  2904.000000  2904.000000   2904.000000   2904.000000    2904.000000   
mean     57.474174     6.206956      5.567149      6.086777  180383.689738   
std      42.724950     2.712204      1.113736      1.410083   79802.823684   
min      20.000000     1.000000      1.000000      1.000000   12789.000000   
25%      20.000000     4.000000      5.000000      5.000000  129150.000000   
50%      50.000000     6.000000      5.000000      6.000000  160000.000000   
75%      70.000000     8.000000      6.000000      7.000000  213000.000000   
max     190.000000    12.000000      9.000000     10.000000  755000.000000   

       TotRms_AbvGrd   Year_Built  Year_Remod/Add      Yr_Sold  
count    2904.000000  2904.000000     2904.000000  2904.000000  
mean        6.441804  1971.109504     1984.112259  2007.792011  
std         1.573130    30.227141       20.857813     1.318719  
min         2.000000  1872.000000     1950.000000  2006.000000  
25%         5.000000  1953.000000     1965.000000  2007.000000  
50%         6.000000  1973.000000     1993.000000  2008.000000  
75%         7.000000  2000.000000     2004.000000  2009.000000  
max        15.000000  2010.000000     2010.000000  2010.000000

In [4]:
import pandas_profiling
df.profile_report()
#
#'''
#Categories of Note: 
#
#'sale_condition'
#'overall_cond'
#'bedroom_abvgr'
#'1st_flr_sf'
#'lot_area'
#'year_built'
#'gr_liv_area'
#'exterior_2nd'
#
#'''

In [5]:
df.columns = map(str.lower, df.columns)

In [6]:
df.yr_sold.head(5)

0    2010
1    2010
2    2010
3    2010
4    2010
Name: yr_sold, dtype: int64

## 1. Do train/test split
Train on houses sold in the years 2006 - 2008. Test on houses sold in the years 2009 - 2010.

In [7]:
df['yr_sold'] = pd.to_datetime(df['yr_sold'], format='%Y')
df['yr_sold'].head(5)

0   2010-01-01
1   2010-01-01
2   2010-01-01
3   2010-01-01
4   2010-01-01
Name: yr_sold, dtype: datetime64[ns]

In [8]:
train = df[df['yr_sold'] < pd.to_datetime(2009, format='%Y')]
test = df[df['yr_sold'] >= pd.to_datetime(2009, format='%Y')]
assert train.shape[0] + test.shape[0] == df.shape[0]

## 2. Begin with baselines

What is the Mean Absolute Error and R^2 score for a mean baseline?

In [9]:
train['saleprice'].mean()

181515.98645833333

In [10]:
df2 = test[['saleprice']]
df2['predicted'] = [181515]*df2.shape[0]

In [11]:
df2['error'] = df2['saleprice'] - df2['predicted']
df2.head(5)

saleprice  predicted  error
0     215000     181515  33485
1     105000     181515 -76515
2     172000     181515  -9515
3     244000     181515  62485
4     189900     181515   8385

In [12]:
df2['error'].mean()

-3340.6697154471544

In [13]:
df2['error'].abs().mean()

58276.60467479675

In [14]:
from sklearn.metrics import r2_score

r2_score(df2['saleprice'], df2['predicted'], multioutput='variance_weighted')

-0.0017912405238886822

## 3. Arrange data into X features matrix and y target vector
Select at least one numeric feature and at least one categorical feature.

## 4. Do one-hot encoding

Encode your categorical feature(s).

In [19]:
import category_encoders as ce

encoder = ce.OneHotEncoder(use_cat_names=True)
encoded = encoder.fit_transform(train['sale_condition'])

encoder2 = ce.OneHotEncoder(use_cat_names=True)
encoded2 = encoder2.fit_transform(train['exterior_2nd'])

In [20]:
encoded.head()

sale_condition_Normal  sale_condition_Family  sale_condition_Abnorml  \
984                      1                      0                       0   
985                      1                      0                       0   
986                      1                      0                       0   
987                      1                      0                       0   
988                      1                      0                       0   

     sale_condition_Partial  sale_condition_Alloca  sale_condition_AdjLand  
984                       0                      0                       0  
985                       0                      0                       0  
986                       0                      0                       0  
987                       0                      0                       0  
988                       0                      0                       0

In [21]:
#Note: Go over with Leo
'''
#feat_num = {
       'AsbShng': 0,
       'AsphShn': 1,
       'BrkComm': 2,
       'BrkFace': 3,
       'CBlock' : 4,
       'CemntBd': 5,
       'HdBoard': 6,
       'ImStucc': 7,
       'MetalSd': 8,
       'Other': 9,
       'Plywood': 10,
       'PreCast': 11,
       'Stone': 12,
       'Stucco': 13,
       'VinylSd': 14,
       'Wd Sdng': 15,
       'WdShing': 16,
}
'''
#df['exterior_1st'] = [feat_num[item] for item in df.exterior_1st]

"\n#feat_num = {\n       'AsbShng': 0,\n       'AsphShn': 1,\n       'BrkComm': 2,\n       'BrkFace': 3,\n       'CBlock' : 4,\n       'CemntBd': 5,\n       'HdBoard': 6,\n       'ImStucc': 7,\n       'MetalSd': 8,\n       'Other': 9,\n       'Plywood': 10,\n       'PreCast': 11,\n       'Stone': 12,\n       'Stucco': 13,\n       'VinylSd': 14,\n       'Wd Sdng': 15,\n       'WdShing': 16,\n}\n"

## 5. Use scikit-learn for Linear Regression
Fit your model.

In [22]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler

model = LinearRegression()
scaler = StandardScaler()

features = ['sale_condition',
            'overall_cond',
            'bedroom_abvgr',
            '1st_flr_sf',
            'lot_area',
            'year_built',
            'gr_liv_area',
            #'exterior_2nd'
           ]
target = 'saleprice'

x_train = scaler.fit_transform(encoder.fit_transform(train[features]))
y_train = train[target]

x_test = scaler.transform(encoder.transform(test[features]))
y_test = test[target]

x_train.shape, y_train.shape

((1920, 12), (1920,))

In [23]:
x_test

array([[ 0.4951123 , -0.13426679, -0.2650172 , ...,  2.75615757,
        -0.36554516,  0.29045724],
       [ 0.4951123 , -0.13426679, -0.2650172 , ...,  0.17478104,
        -0.33240949, -1.16215249],
       [ 0.4951123 , -0.13426679, -0.2650172 , ...,  0.51366038,
        -0.43181651, -0.33454721],
       ...,
       [ 0.4951123 , -0.13426679, -0.2650172 , ...,  0.021933  ,
         0.6947964 , -0.41482301],
       [ 0.4951123 , -0.13426679, -0.2650172 , ..., -0.05622065,
         0.1977613 ,  0.12034899],
       [ 0.4951123 , -0.13426679, -0.2650172 , ...,  0.02552038,
        -0.0673241 ,  0.24458535]])

In [24]:
model.fit(x_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [25]:
y_pred = model.predict(x_test)

## 6. Use regression metrics: MAE, R^2
What is the Mean Absolute Error and R^2 score for your model? ***Beat the mean baseline!***

In [26]:
from sklearn.metrics import mean_absolute_error

In [27]:
mean_absolute_error(y_test, y_pred)
#comparison baseline: 58276.60467479675
#comparison with 2 features: 53663
#added bedrooms_abvgr: 52907
#added 1st_flr_sf: 42535
#added year_built: 33428
#gr_liv_area: 25281


25288.344505632867

In [28]:
#R2
from sklearn.metrics import r2_score

r2_score(y_test, y_pred,
         multioutput='variance_weighted')

0.7739162461430913

## 7. Get coefficients of a linear model
Print or plot the coefficients for the features in your model.

In [29]:
model.coef_

array([-5.19605978e+17, -1.72344074e+17, -3.23580651e+17, -3.94727976e+17,
       -9.86246237e+16, -1.02983076e+17,  1.12160000e+04, -1.10720000e+04,
        1.25920000e+04,  3.07600000e+03,  2.86080000e+04,  4.79200000e+04])

## Stretch Goals
- Try at least 3 different feature combinations.
- Plot exploratory visualizations.
- Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.

In [30]:
#RMSE
from sklearn.metrics import mean_squared_error
from math import sqrt

rms = sqrt(mean_squared_error(y_pred, y_test))
print(rms)

37531.09753737241


In [31]:
#R2
from sklearn.metrics import r2_score

r2_score(y_test, y_pred,
         multioutput='variance_weighted')

0.7739162461430913

## Data Dictionary 

Here's a description of the data fields:

```
1st_Flr_SF: First Floor square feet

Bedroom_AbvGr: Bedrooms above grade (does NOT include basement bedrooms)

Bldg_Type: Type of dwelling
		
       1Fam	Single-family Detached	
       2FmCon	Two-family Conversion; originally built as one-family dwelling
       Duplx	Duplex
       TwnhsE	Townhouse End Unit
       TwnhsI	Townhouse Inside Unit
       
Bsmt_Half_Bath: Basement half bathrooms

Bsmt_Full_Bath: Basement full bathrooms

Central_Air: Central air conditioning

       N	No
       Y	Yes
		
Condition_1: Proximity to various conditions
	
       Artery	Adjacent to arterial street
       Feedr	Adjacent to feeder street	
       Norm	Normal	
       RRNn	Within 200' of North-South Railroad
       RRAn	Adjacent to North-South Railroad
       PosN	Near positive off-site feature--park, greenbelt, etc.
       PosA	Adjacent to postive off-site feature
       RRNe	Within 200' of East-West Railroad
       RRAe	Adjacent to East-West Railroad
	
Condition_2: Proximity to various conditions (if more than one is present)
		
       Artery	Adjacent to arterial street
       Feedr	Adjacent to feeder street	
       Norm	Normal	
       RRNn	Within 200' of North-South Railroad
       RRAn	Adjacent to North-South Railroad
       PosN	Near positive off-site feature--park, greenbelt, etc.
       PosA	Adjacent to postive off-site feature
       RRNe	Within 200' of East-West Railroad
       RRAe	Adjacent to East-West Railroad
       
 Electrical: Electrical system

       SBrkr	Standard Circuit Breakers & Romex
       FuseA	Fuse Box over 60 AMP and all Romex wiring (Average)	
       FuseF	60 AMP Fuse Box and mostly Romex wiring (Fair)
       FuseP	60 AMP Fuse Box and mostly knob & tube wiring (poor)
       Mix	Mixed
       
 Exter_Cond: Evaluates the present condition of the material on the exterior
		
       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor
 
 Exter_Qual: Evaluates the quality of the material on the exterior 
		
       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor
		
Exterior_1st: Exterior covering on house

       AsbShng	Asbestos Shingles
       AsphShn	Asphalt Shingles
       BrkComm	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       CemntBd	Cement Board
       HdBoard	Hard Board
       ImStucc	Imitation Stucco
       MetalSd	Metal Siding
       Other	Other
       Plywood	Plywood
       PreCast	PreCast	
       Stone	Stone
       Stucco	Stucco
       VinylSd	Vinyl Siding
       Wd Sdng	Wood Siding
       WdShing	Wood Shingles
	
Exterior_2nd: Exterior covering on house (if more than one material)

       AsbShng	Asbestos Shingles
       AsphShn	Asphalt Shingles
       BrkComm	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       CemntBd	Cement Board
       HdBoard	Hard Board
       ImStucc	Imitation Stucco
       MetalSd	Metal Siding
       Other	Other
       Plywood	Plywood
       PreCast	PreCast
       Stone	Stone
       Stucco	Stucco
       VinylSd	Vinyl Siding
       Wd Sdng	Wood Siding
       WdShing	Wood Shingles
       
Foundation: Type of foundation
		
       BrkTil	Brick & Tile
       CBlock	Cinder Block
       PConc	Poured Contrete	
       Slab	Slab
       Stone	Stone
       Wood	Wood
		
Full_Bath: Full bathrooms above grade

Functional: Home functionality (Assume typical unless deductions are warranted)

       Typ	Typical Functionality
       Min1	Minor Deductions 1
       Min2	Minor Deductions 2
       Mod	Moderate Deductions
       Maj1	Major Deductions 1
       Maj2	Major Deductions 2
       Sev	Severely Damaged
       Sal	Salvage only
		
Gr_Liv_Area: Above grade (ground) living area square feet
        
Half_Bath: Half baths above grade

Heating: Type of heating
		
       Floor	Floor Furnace
       GasA	Gas forced warm air furnace
       GasW	Gas hot water or steam heat
       Grav	Gravity furnace	
       OthW	Hot water or steam heat other than gas
       Wall	Wall furnace
		
Heating_QC: Heating quality and condition

       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor

House_Style: Style of dwelling
	
       1Story	One story
       1.5Fin	One and one-half story: 2nd level finished
       1.5Unf	One and one-half story: 2nd level unfinished
       2Story	Two story
       2.5Fin	Two and one-half story: 2nd level finished
       2.5Unf	Two and one-half story: 2nd level unfinished
       SFoyer	Split Foyer
       SLvl	Split Level

Kitchen_AbvGr: Kitchens above grade

Kitchen_Qual: Kitchen quality

       Ex	Excellent
       Gd	Good
       TA	Typical/Average
       Fa	Fair
       Po	Poor

LandContour: Flatness of the property

       Lvl	Near Flat/Level	
       Bnk	Banked - Quick and significant rise from street grade to building
       HLS	Hillside - Significant slope from side to side
       Low	Depression
		
Land_Slope: Slope of property
		
       Gtl	Gentle slope
       Mod	Moderate Slope	
       Sev	Severe Slope

Lot_Area: Lot size in square feet

Lot_Config: Lot configuration

       Inside	Inside lot
       Corner	Corner lot
       CulDSac	Cul-de-sac
       FR2	Frontage on 2 sides of property
       FR3	Frontage on 3 sides of property

Lot_Shape: General shape of property

       Reg	Regular	
       IR1	Slightly irregular
       IR2	Moderately Irregular
       IR3	Irregular

MS_SubClass: Identifies the type of dwelling involved in the sale.	

        20	1-STORY 1946 & NEWER ALL STYLES
        30	1-STORY 1945 & OLDER
        40	1-STORY W/FINISHED ATTIC ALL AGES
        45	1-1/2 STORY - UNFINISHED ALL AGES
        50	1-1/2 STORY FINISHED ALL AGES
        60	2-STORY 1946 & NEWER
        70	2-STORY 1945 & OLDER
        75	2-1/2 STORY ALL AGES
        80	SPLIT OR MULTI-LEVEL
        85	SPLIT FOYER
        90	DUPLEX - ALL STYLES AND AGES
       120	1-STORY PUD (Planned Unit Development) - 1946 & NEWER
       150	1-1/2 STORY PUD - ALL AGES
       160	2-STORY PUD - 1946 & NEWER
       180	PUD - MULTILEVEL - INCL SPLIT LEV/FOYER
       190	2 FAMILY CONVERSION - ALL STYLES AND AGES

MS_Zoning: Identifies the general zoning classification of the sale.
		
       A	Agriculture
       C	Commercial
       FV	Floating Village Residential
       I	Industrial
       RH	Residential High Density
       RL	Residential Low Density
       RP	Residential Low Density Park 
       RM	Residential Medium Density

Mas_Vnr_Type: Masonry veneer type

       BrkCmn	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       None	None
       Stone	Stone

Mo_Sold: Month Sold (MM)

Neighborhood: Physical locations within Ames city limits

       Blmngtn	Bloomington Heights
       Blueste	Bluestem
       BrDale	Briardale
       BrkSide	Brookside
       ClearCr	Clear Creek
       CollgCr	College Creek
       Crawfor	Crawford
       Edwards	Edwards
       Gilbert	Gilbert
       IDOTRR	Iowa DOT and Rail Road
       MeadowV	Meadow Village
       Mitchel	Mitchell
       Names	North Ames
       NoRidge	Northridge
       NPkVill	Northpark Villa
       NridgHt	Northridge Heights
       NWAmes	Northwest Ames
       OldTown	Old Town
       SWISU	South & West of Iowa State University
       Sawyer	Sawyer
       SawyerW	Sawyer West
       Somerst	Somerset
       StoneBr	Stone Brook
       Timber	Timberland
       Veenker	Veenker
			
Overall_Cond: Rates the overall condition of the house

       10	Very Excellent
       9	Excellent
       8	Very Good
       7	Good
       6	Above Average	
       5	Average
       4	Below Average	
       3	Fair
       2	Poor
       1	Very Poor

Overall_Qual: Rates the overall material and finish of the house

       10	Very Excellent
       9	Excellent
       8	Very Good
       7	Good
       6	Above Average
       5	Average
       4	Below Average
       3	Fair
       2	Poor
       1	Very Poor

Paved_Drive: Paved driveway

       Y	Paved 
       P	Partial Pavement
       N	Dirt/Gravel

Roof_Matl: Roof material

       ClyTile	Clay or Tile
       CompShg	Standard (Composite) Shingle
       Membran	Membrane
       Metal	Metal
       Roll	Roll
       Tar&Grv	Gravel & Tar
       WdShake	Wood Shakes
       WdShngl	Wood Shingles

Roof_Style: Type of roof

       Flat	Flat
       Gable	Gable
       Gambrel	Gabrel (Barn)
       Hip	Hip
       Mansard	Mansard
       Shed	Shed

SalePrice: the sales price for each house

Sale_Condition: Condition of sale

       Normal	Normal Sale
       Abnorml	Abnormal Sale -  trade, foreclosure, short sale
       AdjLand	Adjoining Land Purchase
       Alloca	Allocation - two linked properties with separate deeds, typically condo with a garage unit	
       Family	Sale between family members
       Partial	Home was not completed when last assessed (associated with New Homes)

Sale_Type: Type of sale
		
       WD 	Warranty Deed - Conventional
       CWD	Warranty Deed - Cash
       VWD	Warranty Deed - VA Loan
       New	Home just constructed and sold
       COD	Court Officer Deed/Estate
       Con	Contract 15% Down payment regular terms
       ConLw	Contract Low Down payment and low interest
       ConLI	Contract Low Interest
       ConLD	Contract Low Down
       Oth	Other
	
Street: Type of road access to property

       Grvl	Gravel	
       Pave	Paved
       	
TotRms_AbvGrd: Total rooms above grade (does not include bathrooms)

Utilities: Type of utilities available
		
       AllPub	All public Utilities (E,G,W,& S)	
       NoSewr	Electricity, Gas, and Water (Septic Tank)
       NoSeWa	Electricity and Gas Only
       ELO	Electricity only	
	
Year_Built: Original construction date

Year_Remod/Add: Remodel date (same as construction date if no remodeling or additions)
						
Yr_Sold: Year Sold (YYYY)	

```